<a href="https://colab.research.google.com/github/ramayer/google-colab-examples/blob/main/tmp/osm_in_spark_working_in_colab.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Spark with GIS visualization In Kaggle Notebooks.

In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

In [2]:
required_packages = {"keplergl","geopandas","h3","geocoder"}

import pkg_resources
for lib in required_packages - {pkg.key for pkg in pkg_resources.working_set}:
  print(f"installing {lib}")
  %pip install -q --upgrade pip
  %pip install --use-feature=2020-resolver -q $lib

installing geopandas
     |████████████████████████████████| 1.5MB 10.0MB/s 
     |████████████████████████████████| 994 kB 8.8 MB/s 
     |████████████████████████████████| 6.5 MB 24.2 MB/s 
     |████████████████████████████████| 14.8 MB 147 kB/s 
installing h3
     |████████████████████████████████| 793 kB 8.1 MB/s 
installing keplergl
     |████████████████████████████████| 7.9 MB 6.9 MB/s 
installing geocoder
     |████████████████████████████████| 98 kB 4.0 MB/s 


In [3]:
%%sh
df

Filesystem     1K-blocks     Used Available Use% Mounted on
overlay        113008892 40361252  72631256  36% /
tmpfs              65536        0     65536   0% /dev
tmpfs            6666784        0   6666784   0% /sys/fs/cgroup
shm              6160384        0   6160384   0% /dev/shm
tmpfs            6666784       24   6666760   1% /var/colab
/dev/sda1      119512108 42181116  77314608  36% /etc/hosts
tmpfs            6666784        0   6666784   0% /proc/acpi
tmpfs            6666784        0   6666784   0% /proc/scsi
tmpfs            6666784        0   6666784   0% /sys/firmware


In [4]:
!sh -c ls

sample_data


In [5]:
!pip install pyspark

     |████████████████████████████████| 212.3 MB 15 kB/s 
     |████████████████████████████████| 198 kB 51.4 MB/s 
  Created wheel for pyspark: filename=pyspark-3.1.1-py2.py3-none-any.whl size=212767604 sha256=b83d9616c3859daae0b64ff33f08b65086ec08b690a267936da0ed5a743e3d13
  Stored in directory: /root/.cache/pip/wheels/43/47/42/bc413c760cf9d3f7b46ab7cd6590e8c47ebfd19a7386cd4a57
Successfully built pyspark


In [6]:
import pyspark

MAX_MEMORY = "8g"  # 24 gives OOM here.

spark = (pyspark.sql.SparkSession.builder.appName("MyApp") 
    .config("spark.jars.packages", "io.delta:delta-core_2.12:0.8.0") 
    .config("spark.sql.extensions", "io.delta.sql.DeltaSparkSessionExtension") 
    .config("spark.sql.catalog.spark_catalog", "org.apache.spark.sql.delta.catalog.DeltaCatalog") 
    .config("spark.executor.memory", MAX_MEMORY) 
    .config("spark.driver.memory", MAX_MEMORY) 
    .enableHiveSupport() 
    .getOrCreate()        
    )
spark

In [7]:
df = spark.createDataFrame([{'hi':'hello','w':'world'}])

In [8]:
 df.write.format('delta').mode('overwrite').option("mergeSchema", "true").save('/tmp/delta1')

In [9]:
df = spark.read.format('delta').load('/tmp/delta1')
df.createOrReplaceTempView('d1')
spark.sql('select * from d1').toPandas()

hi      w
0  hello  world

In [10]:
!(cd /tmp; wget -nc -q --show-progres https://download.geofabrik.de/north-america/us/hawaii-latest.osm.pbf)

hawaii-latest.osm.p 100%[===================>]  14.43M  8.90MB/s    in 1.6s    


In [11]:
!apt-get install -y maven


Reading package lists... Done
Building dependency tree       
Reading state information... Done
The following additional packages will be installed:
  libaopalliance-java libapache-pom-java libatinject-jsr330-api-java
  libcdi-api-java libcommons-cli-java libcommons-io-java libcommons-lang3-java
  libcommons-parent-java libgeronimo-annotation-1.3-spec-java
  libgeronimo-interceptor-3.0-spec-java libguava-java libguice-java
  libhawtjni-runtime-java libjansi-java libjansi-native-java libjsr305-java
  libmaven-parent-java libmaven-resolver-java libmaven-shared-utils-java
  libmaven3-core-java libplexus-cipher-java libplexus-classworlds-java
  libplexus-component-annotations-java libplexus-interpolation-java
  libplexus-sec-dispatcher-java libplexus-utils2-java libsisu-inject-java
  libsisu-plexus-java libslf4j-java libwagon-file-java
  libwagon-http-shaded-java libwagon-provider-api-java
Suggested packages:
  libaopalliance-java-doc libatinject-jsr330-api-java-doc libservlet3.1-java
  li

In [12]:
!git clone https://github.com/adrianulbona/osm-parquetizer.git


Cloning into 'osm-parquetizer'...
remote: Enumerating objects: 20, done.
remote: Counting objects: 100% (20/20), done.
remote: Compressing objects: 100% (13/13), done.
remote: Total 219 (delta 2), reused 9 (delta 0), pack-reused 199
Receiving objects: 100% (219/219), 80.46 KiB | 5.75 MiB/s, done.
Resolving deltas: 100% (70/70), done.


In [13]:
!(cd osm-parquetizer; mvn clean package)


[INFO] Scanning for projects...
[INFO] 
[INFO] ---------------< io.github.adrianulbona:osm-parquetizer >---------------
[INFO] Building OSM Parquetizer 1.0.1-SNAPSHOT
[INFO] --------------------------------[ jar ]---------------------------------
Downloaded from central: https://repo.maven.apache.org/maven2/org/apache/maven/plugins/maven-clean-plugin/2.5/maven-clean-plugin-2.5.pom (3.9 kB at 7.1 kB/s)
Downloaded from central: https://repo.maven.apache.org/maven2/org/apache/maven/plugins/maven-plugins/22/maven-plugins-22.pom (13 kB at 310 kB/s)
Downloaded from central: https://repo.maven.apache.org/maven2/org/apache/maven/maven-parent/21/maven-parent-21.pom (26 kB at 643 kB/s)
Downloaded from central: https://repo.maven.apache.org/maven2/org/apache/apache/10/apache-10.pom (15 kB at 548 kB/s)
Downloaded from central: https://repo.maven.apache.org/maven2/org/apache/maven/plugins/maven-clean-plugin/2.5/maven-clean-plugin-2.5.jar (25 kB at 425 kB/s)
Downloaded from central: https://repo.mav

In [15]:
!java -jar ./osm-parquetizer/target/osm-parquetizer-1.0.1-SNAPSHOT.jar /tmp/hawaii-latest.osm.pbf


2021-03-15 02:31:43 WARN  NativeCodeLoader:60 - Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
2021-03-15 02:31:44 INFO  CodecPool:153 - Got brand-new compressor [.snappy]
2021-03-15 02:31:44 INFO  CodecPool:153 - Got brand-new compressor [.snappy]
2021-03-15 02:31:44 INFO  CodecPool:153 - Got brand-new compressor [.snappy]
2021-03-15 02:31:48 INFO  App$MultiEntitySinkObserver:118 - Entities processed: 1000000
2021-03-15 02:31:50 INFO  App$MultiEntitySinkObserver:118 - Entities processed: 2000000
2021-03-15 02:31:53 INFO  App$MultiEntitySinkObserver:125 - Total entities processed: 2205928


In [17]:
!ls -lrt /tmp

total 68976
-rw-r--r--  1 root root 15134938 Mar 13 23:28 hawaii-latest.osm.pbf
lrwxrwxrwx  1 root root       61 Mar 15 02:25 dap_multiplexer.INFO -> dap_multiplexer.a78658af307a.root.log.INFO.20210315-022539.50
srwxr-xr-x  1 root root        0 Mar 15 02:25 debugger_15z3ac91s2
drwx------  2 root root     4096 Mar 15 02:25 initgoogle_syslog_dir.0
-rw-r--r--  1 root root     1498 Mar 15 02:25 dap_multiplexer.a78658af307a.root.log.INFO.20210315-022539.50
drwxr-xr-x  2 root root     4096 Mar 15 02:28 spark-7f20db94-e23f-420d-b42f-33670a3d493f
drwx------  4 root root     4096 Mar 15 02:28 spark-846c87d2-ab3e-4104-a7cb-ecc0af207798
-rw-r--r--  1 root root        0 Mar 15 02:28 liblz4-java-19740598505995443.so.lck
-rw-r--r--  1 root root   203408 Mar 15 02:28 liblz4-java-19740598505995443.so
drwxr-xr-x  3 root root     4096 Mar 15 02:28 delta1
-rwxr--r--  1 root root   281680 Mar 15 02:28 snappy-1.1.8-7bf5da55-2951-4f80-9582-683dee6cc211-libsnappyjava.so
drwxr-xr-x 64 root root     4096 Mar 1

In [20]:
df = spark.sql("select * from parquet.`/tmp/hawaii-latest.osm.pbf.node.parquet` order by size(tags) desc")
df.createOrReplaceTempView('orig_osm_nodes')

In [23]:
named_nodes =spark.sql('''select * from orig_osm_nodes where size(tags)>0''').selectExpr('''
  map_from_arrays(transform(tags,x -> decode(x['key'],'utf-8')),transform(tags,x -> decode(x['value'],'utf-8'))) as tagmap
  ''','*').selectExpr("element_at(tagmap,'name') as n",'*').drop('tags')
named_nodes.show(5)

+--------------------+--------------------+----------+-------+-------------+---------+---+--------+------------------+-------------------+
|                   n|              tagmap|        id|version|    timestamp|changeset|uid|user_sid|          latitude|          longitude|
+--------------------+--------------------+----------+-------+-------------+---------+---+--------+------------------+-------------------+
|              Hawaii|{alt_name:vi -> H...| 316949921|     33|1609745200000|        0|  0|      []|        21.2160437|-157.97520300000002|
| Church of God (WMC)|{fax -> +82 31 73...|3831920861|      1|1447289605000|        0|  0|      []|21.335132400000003|       -157.9073993|
|Revtek Speed Tuni...|{name -> Revtek S...|6764798989|      2|1588576430000|        0|  0|      []|        21.4213846|       -158.0062521|
|       Teapresso Bar|{addr:city -> Hil...|7709896619|      8|1614485132000|        0|  0|      []|        19.7072301|-155.07546340000002|
|Big Island Pearl Tea|{addr

In [30]:
required_packages = {"keplergl","geopandas","h3","geocoder"}
import pkg_resources
for lib in required_packages - {pkg.key for pkg in pkg_resources.working_set}:
  print(f"installing {lib}")
  # dbutils.library.installPyPI("azure-identity")  # for older Databricks Runtimes.
  %pip install -q --upgrade pip
  %pip install -q $lib  # for older Databricks Runtimes.


installing geopandas
installing h3
installing keplergl
installing geocoder


In [25]:
#import h3
import h3.api.basic_int as h3
import pandas as pd
import pyspark.sql.functions as psf
@psf.pandas_udf('string')
def h3_parent_udf(h:pd.Series,lvl:pd.Series) -> pd.Series:
  parents = [h3.h3_to_parent(a,b) for a,b in zip(h,lvl)]
  return pd.Series(parents)

@psf.pandas_udf('string')
def geo_to_h3_udf(lat:pd.Series,lon:pd.Series,lvl:pd.Series) -> pd.Series:
  res = [h3.geo_to_h3(a,b,c) for a,b,c in zip(lat,lon,lvl)]
  return pd.Series(res)

@psf.pandas_udf('array<bigint>')
def geo_to_h3s_udf(lat:pd.Series,lon:pd.Series) -> pd.Series:
  res = [[h3.geo_to_h3(a,b,l) for l in range(15)] for a,b in zip(lat,lon)]
  return pd.Series(res)

@psf.pandas_udf("lat:float,lon:float")
def h3_to_geo_udf(s: pd.Series) -> pd.DataFrame:
  result = s.apply(lambda x: h3.h3_to_geo(x))
  return pd.DataFrame(list(result))

spark.udf.register("geo_to_h3s", geo_to_h3s_udf)
spark.udf.register("geo_to_h3", geo_to_h3_udf)
spark.udf.register("h3_to_geo", h3_to_geo_udf)
spark.udf.register("h3_parent", h3_parent_udf)

<function __main__.h3_parent_udf>

In [26]:
df = spark.sql('''select latitude,longitude,geo_to_h3s(latitude,longitude) as h3s from orig_osm_nodes''')
df.write.format('delta').saveAsTable('tmp_osm_with_h3')

In [28]:
df = spark.sql("select * from tmp_osm_with_h3")
display(df)
df.show(5)

DataFrame[latitude: double, longitude: double, h3s: array<bigint>]

+------------------+-------------------+--------------------+
|          latitude|          longitude|                 h3s|
+------------------+-------------------+--------------------+
|        21.3068044|-157.91076800000002|[5781144177915985...|
|21.309688400000002|       -157.9110345|[5781144177915985...|
|21.309699600000002|       -157.9456652|[5781144177915985...|
|        21.3230502|       -157.9431932|[5781144177915985...|
|        21.2712307|       -157.8226339|[5781144177915985...|
+------------------+-------------------+--------------------+
only showing top 5 rows



In [50]:
data_for_map = spark.sql('''select hex(h3s[8]) as h3,count(*) as num_in_grid from tmp_osm_with_h3 group by h3''')

import keplergl
map_1 = keplergl.KeplerGl(height=600)
map_1.add_data(data = data_for_map.toPandas(), name = "h3")
map_1

User Guide: https://docs.kepler.gl/docs/keplergl-jupyter


KeplerGl(data={'h3': {'index': [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, …

In [51]:
resize_for_databricks = '''
  <script>
    var targetHeight = "600px";
    window.setInterval(function() {{
      if (document.body && document.body.style && document.body.style.height !== targetHeight) {{
        document.body.style.height = targetHeight;
      }}
    }}, 2500)
    </script>
    '''
orig_html   = keplergl.KeplerGl._repr_html_(map_1)
better_html = (str(orig_html,'utf-8') + resize_for_databricks)

import base64
b64 = base64.b64encode(better_html.encode('utf-8'))
src = f"data:text/html;base64,{b64.decode('utf-8')}"
base64d_html = f'<iframe src="{src}" style="width:100%; height: 600px">'


In [52]:

from IPython.core.display import HTML
HTML(base64d_html)